# スタッキング
・GBDT 2~3個：決定木の深さが「浅い」「普通」「深い」モデル

・Random Forest 1~2個：決定木の深さが「浅い」「深い」モデル

・Neural Net 1~2個：層の数が「少ない」「多い」モデル

・Linier 1個

In [3]:
import os
os.chdir('../../')

In [4]:
import numpy as np
import pandas as pd
from scr.util import *
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
from scr.models.gbdt import Model1_CatBoost_1, Model1_CatBoost_2, Model1_CatBoost_3, Model1_XGBoost_1, Model1_XGBoost_2, Model1_XGBoost_3, Model1_LightGBM_1, Model1_LightGBM_2, Model1_LightGBM_3
from scr.models.random_forest import Model1_RandomForest_1, Model1_RandomForest_2, Model1_RandomForest_3
from scr.models.nn import Model1_NN_1, Model1_NN_2, Model1_NN_all_1, Model1_NN_all_2, Model1_TabNet_1, Model1_TabNet_2
from scr.models.linear import Model1_Logistic_1, Model1_Logistic_2, Model1_Logistic_3, Model1_Logistic_4, Model2_Logistic

In [5]:
path_gb = 'data/sampling/under_sampling/mean_gb'
path_nn = 'data/sampling/under_sampling/mean_nn'

files_gb = os.listdir(path_gb)
files_nn = os.listdir(path_nn)

trains_gb = []
for file in files_gb:
    file_path = os.path.join(path_gb, file)
    df = pd.read_csv(file_path)
    trains_gb.append(df)

trains_nn = []
for file in files_nn:
    file_path = os.path.join(path_nn, file)
    df = pd.read_csv(file_path)
    trains_nn.append(df)

In [6]:
train_gb = trains_gb[0]
test_gb = pd.read_csv('data/feature_engineered/null_representative/test_null_mean.csv')

train_nn = trains_nn[0]
test_nn = pd.read_csv('data/feature_engineered/null_representative/test_null_mean_scaled.csv')

combination_columns = train_gb.columns[44:110]
y = train_gb['ProdTaken']

In [7]:
# 特徴量が多いので、落とす特徴量を選択
drop_gb = [
    'EconomicSegment',
    'ContractRate_FM',
    'ContractRate_G1',
    'ContractRate_G2',
    'ContractRate_G3',
    'ContractRate_G4',
    'ContractRate_G5',
    'ContractRate_G6'
]

## --------------------------------------------------------------------------------------------
## Label Encoding
train_gb = mapping_columns_if_exist(train_gb)
test_gb = mapping_columns_if_exist(test_gb)

def handle_unknown_label(train_series, test_series):
    unique_labels = train_series.unique()
    label_map = {label: idx for idx, label in enumerate(unique_labels)}
    train_encoded = train_series.map(label_map)
    test_encoded = test_series.map(lambda x: label_map.get(x, -1))
    return train_encoded, test_encoded

for col in combination_columns:
    train_gb[col], test_gb[col] = handle_unknown_label(train_gb[col], test_gb[col])
## --------------------------------------------------------------------------------------------

X_gb = train_gb.drop(columns=drop_gb, axis=1)
y_gb = train_gb['ProdTaken']

test_feature = X_gb.columns.drop('ProdTaken')
test_gb = test_gb[test_feature]

tmp = X_gb.groupby(by=['AgeGroup', 'ProductPitched'], as_index=False)['ProdTaken'].mean()
tmp = tmp.rename(columns={'ProdTaken': 'ContractRate_G4'})
test_gb = test_gb.merge(tmp, on=['AgeGroup', 'ProductPitched'], how='left')

In [8]:
drop_nn = [
    'EconomicSegment',
    'ContractRate_FM',
    'ContractRate_G1',
    'ContractRate_G2',
    'ContractRate_G3',
    'ContractRate_G4',
    'ContractRate_G5',
    'ContractRate_G6'
]

X_nn = train_nn.drop(columns=drop_nn, axis=1)
X_nn = X_nn.drop(columns=['ProdTaken'])
y_nn = train_nn['ProdTaken']

test_nn = test_nn.drop(columns=drop_nn, axis=1)

num_features_nn = len(test_nn.columns)

In [9]:
# スタッキング
def predict_cv(model, X, y, df_test):
    preds = []
    preds_test = []
    va_idxes = []

    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=0)

    for i, (tr_idx, va_idx) in enumerate(skf.split(X, y)):
        tr_x, va_x = X.iloc[tr_idx], X.iloc[va_idx]
        tr_y, va_y = y.iloc[tr_idx], y.iloc[va_idx]
        
        # Target Encoding
        if 'AgeGroup' in tr_x.columns:
            tmp = tr_x.groupby(by=['AgeGroup', 'ProductPitched'], as_index=False)['ProdTaken'].mean()
            tmp = tmp.rename(columns={'ProdTaken': 'ContractRate_G4'})
            tr_x = tr_x.merge(tmp, on=['AgeGroup', 'ProductPitched'], how='left')
            va_x = va_x.merge(tmp, on=['AgeGroup', 'ProductPitched'], how='left')
            
            tr_x = tr_x.drop(labels='ProdTaken', axis=1)
            va_x = va_x.drop(labels='ProdTaken', axis=1)
        
        model.fit(tr_x, tr_y, va_x, va_y)
        pred = model.predict(va_x)
        preds.append(pred)
        pred_test = model.predict(df_test)
        preds_test.append(pred_test)
        va_idxes.append(va_idx)

    # バリデーションデータに対する予測値を連結し、その後元の順序に並べ直す
    va_idxes = np.concatenate(va_idxes)
    preds = np.concatenate(preds, axis=0)
    order = np.argsort(va_idxes)
    pred_train = preds[order]

    # テストデータに対する予測値の平均をとる
    preds_test = np.mean(preds_test, axis=0)

    return pred_train, preds_test

In [10]:
# 1層目のモデル
models_gbdt = [
    Model1_CatBoost_1(),
    Model1_CatBoost_2(),
    Model1_CatBoost_3(),
    Model1_XGBoost_1(),
    Model1_XGBoost_2(),
    Model1_XGBoost_3(),
    Model1_LightGBM_1(),
    Model1_LightGBM_2(),
    Model1_LightGBM_3()
]

models_nn = [
    Model1_RandomForest_1(),
    Model1_RandomForest_2(),
    Model1_RandomForest_3(),
    Model1_NN_1(input_shape=num_features_nn),
    Model1_NN_2(input_shape=num_features_nn),
    Model1_NN_all_1(input_shape=num_features_nn),
    Model1_NN_all_2(input_shape=num_features_nn),
    Model1_TabNet_1(input_dim=num_features_nn),
    Model1_TabNet_2(input_dim=num_features_nn),
    Model1_Logistic_1(),
    Model1_Logistic_2(),
    Model1_Logistic_3(),
    Model1_Logistic_4()
]

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")


In [11]:
pred_train_list = []
pred_test_list = []

for model in models_gbdt:
    pred_train, pred_test = predict_cv(model, X_gb, y_gb, test_gb)
    pred_train_list.append(pred_train)
    pred_test_list.append(pred_test)

for model in models_nn:
    pred_train, pred_test = predict_cv(model, X_nn, y_nn, test_nn)
    pred_train_list.append(pred_train)
    pred_test_list.append(pred_test)

0:	test: 0.7807083	best: 0.7807083 (0)	total: 143ms	remaining: 11m 52s
200:	test: 0.8464167	best: 0.8470000 (12)	total: 665ms	remaining: 15.9s
400:	test: 0.8471667	best: 0.8490000 (326)	total: 1.1s	remaining: 12.6s
600:	test: 0.8467500	best: 0.8490000 (326)	total: 1.51s	remaining: 11.1s
800:	test: 0.8459167	best: 0.8490000 (326)	total: 1.92s	remaining: 10s
1000:	test: 0.8425833	best: 0.8490000 (326)	total: 2.34s	remaining: 9.35s
1200:	test: 0.8412500	best: 0.8490000 (326)	total: 2.75s	remaining: 8.7s
1400:	test: 0.8387500	best: 0.8490000 (326)	total: 3.14s	remaining: 8.06s
1600:	test: 0.8356667	best: 0.8490000 (326)	total: 3.54s	remaining: 7.51s
1800:	test: 0.8351667	best: 0.8490000 (326)	total: 3.93s	remaining: 6.97s
2000:	test: 0.8341667	best: 0.8490000 (326)	total: 4.29s	remaining: 6.42s
2200:	test: 0.8334167	best: 0.8490000 (326)	total: 4.66s	remaining: 5.92s
2400:	test: 0.8324167	best: 0.8490000 (326)	total: 5.01s	remaining: 5.42s
2600:	test: 0.8315000	best: 0.8490000 (326)	total:

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


epoch 0  | loss: 0.99558 | val_0_auc: 0.46664 |  0:00:00s
epoch 1  | loss: 0.87897 | val_0_auc: 0.39992 |  0:00:00s
epoch 2  | loss: 0.84275 | val_0_auc: 0.44571 |  0:00:01s
epoch 3  | loss: 0.80723 | val_0_auc: 0.55664 |  0:00:01s
epoch 4  | loss: 0.80889 | val_0_auc: 0.57731 |  0:00:02s
epoch 5  | loss: 0.77126 | val_0_auc: 0.61672 |  0:00:02s
epoch 6  | loss: 0.73726 | val_0_auc: 0.66151 |  0:00:02s
epoch 7  | loss: 0.71627 | val_0_auc: 0.57605 |  0:00:03s
epoch 8  | loss: 0.72037 | val_0_auc: 0.55748 |  0:00:03s
epoch 9  | loss: 0.68306 | val_0_auc: 0.54416 |  0:00:04s
epoch 10 | loss: 0.67739 | val_0_auc: 0.56269 |  0:00:04s
epoch 11 | loss: 0.66045 | val_0_auc: 0.59521 |  0:00:04s
epoch 12 | loss: 0.66932 | val_0_auc: 0.62945 |  0:00:05s
epoch 13 | loss: 0.66655 | val_0_auc: 0.6916  |  0:00:05s
epoch 14 | loss: 0.66316 | val_0_auc: 0.71353 |  0:00:05s
epoch 15 | loss: 0.65787 | val_0_auc: 0.74975 |  0:00:06s
epoch 16 | loss: 0.64755 | val_0_auc: 0.76706 |  0:00:06s
epoch 17 | los

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


epoch 0  | loss: 1.03383 | val_0_auc: 0.52795 |  0:00:00s
epoch 1  | loss: 0.89154 | val_0_auc: 0.41608 |  0:00:00s
epoch 2  | loss: 0.88667 | val_0_auc: 0.45202 |  0:00:01s
epoch 3  | loss: 0.80514 | val_0_auc: 0.43889 |  0:00:01s
epoch 4  | loss: 0.77397 | val_0_auc: 0.48687 |  0:00:02s
epoch 5  | loss: 0.80044 | val_0_auc: 0.4952  |  0:00:02s
epoch 6  | loss: 0.79325 | val_0_auc: 0.4984  |  0:00:02s
epoch 7  | loss: 0.76745 | val_0_auc: 0.51709 |  0:00:03s
epoch 8  | loss: 0.74664 | val_0_auc: 0.52601 |  0:00:03s
epoch 9  | loss: 0.71667 | val_0_auc: 0.54247 |  0:00:03s
epoch 10 | loss: 0.67249 | val_0_auc: 0.55665 |  0:00:04s
epoch 11 | loss: 0.69564 | val_0_auc: 0.56734 |  0:00:04s
epoch 12 | loss: 0.66269 | val_0_auc: 0.5904  |  0:00:05s
epoch 13 | loss: 0.6837  | val_0_auc: 0.6202  |  0:00:05s
epoch 14 | loss: 0.68694 | val_0_auc: 0.6798  |  0:00:05s
epoch 15 | loss: 0.64298 | val_0_auc: 0.72593 |  0:00:06s
epoch 16 | loss: 0.65439 | val_0_auc: 0.75471 |  0:00:06s
epoch 17 | los

...

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


epoch 0  | loss: 1.43089 | val_0_auc: 0.54141 |  0:00:00s
epoch 1  | loss: 1.18238 | val_0_auc: 0.47921 |  0:00:01s
epoch 2  | loss: 1.09865 | val_0_auc: 0.45816 |  0:00:01s
epoch 3  | loss: 1.1979  | val_0_auc: 0.46827 |  0:00:02s
epoch 4  | loss: 1.02461 | val_0_auc: 0.49301 |  0:00:03s
epoch 5  | loss: 0.9947  | val_0_auc: 0.57146 |  0:00:03s
epoch 6  | loss: 0.86168 | val_0_auc: 0.683   |  0:00:04s
epoch 7  | loss: 0.86913 | val_0_auc: 0.70177 |  0:00:04s
epoch 8  | loss: 0.85646 | val_0_auc: 0.72753 |  0:00:05s
epoch 9  | loss: 0.87556 | val_0_auc: 0.72391 |  0:00:06s
epoch 10 | loss: 0.80347 | val_0_auc: 0.69992 |  0:00:06s
epoch 11 | loss: 0.81482 | val_0_auc: 0.67374 |  0:00:07s
epoch 12 | loss: 0.80223 | val_0_auc: 0.66574 |  0:00:08s
epoch 13 | loss: 0.81927 | val_0_auc: 0.67239 |  0:00:08s
epoch 14 | loss: 0.8151  | val_0_auc: 0.67795 |  0:00:09s
epoch 15 | loss: 0.80148 | val_0_auc: 0.68687 |  0:00:09s
epoch 16 | loss: 0.73235 | val_0_auc: 0.65926 |  0:00:10s
epoch 17 | los

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


epoch 0  | loss: 1.48342 | val_0_auc: 0.54167 |  0:00:00s
epoch 1  | loss: 1.06567 | val_0_auc: 0.62811 |  0:00:01s
epoch 2  | loss: 1.03628 | val_0_auc: 0.63889 |  0:00:01s
epoch 3  | loss: 1.22321 | val_0_auc: 0.63443 |  0:00:02s
epoch 4  | loss: 1.08696 | val_0_auc: 0.56852 |  0:00:03s
epoch 5  | loss: 0.9526  | val_0_auc: 0.5947  |  0:00:03s
epoch 6  | loss: 0.96787 | val_0_auc: 0.62365 |  0:00:04s
epoch 7  | loss: 1.00069 | val_0_auc: 0.65    |  0:00:04s
epoch 8  | loss: 1.00452 | val_0_auc: 0.6617  |  0:00:05s
epoch 9  | loss: 0.94216 | val_0_auc: 0.64756 |  0:00:06s
epoch 10 | loss: 0.86078 | val_0_auc: 0.658   |  0:00:06s
epoch 11 | loss: 0.82547 | val_0_auc: 0.64091 |  0:00:07s
epoch 12 | loss: 0.80805 | val_0_auc: 0.64343 |  0:00:07s
epoch 13 | loss: 0.90869 | val_0_auc: 0.63258 |  0:00:08s
epoch 14 | loss: 0.84036 | val_0_auc: 0.62668 |  0:00:09s
epoch 15 | loss: 0.79814 | val_0_auc: 0.65505 |  0:00:09s
epoch 16 | loss: 0.75162 | val_0_auc: 0.67492 |  0:00:10s
epoch 17 | los

c:\Users\ricke\anaconda3\envs\neuralnet\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


In [12]:
# 1層目のモデルの評価
for i, pred_train in enumerate(pred_train_list):
    auc_score = roc_auc_score(y, pred_train)
    print(f'AUC for model {i+1}: {auc_score}')

AUC for model 1: 0.8229477029119626
AUC for model 2: 0.7964414198043015
AUC for model 3: 0.801029885489901
AUC for model 4: 0.7826525093801541
AUC for model 5: 0.7864012119461342
AUC for model 6: 0.7893303057073662
AUC for model 7: 0.8039153115689126
AUC for model 8: 0.7981243050960184
AUC for model 9: 0.7980806374137983
AUC for model 10: 0.8132165278818151
AUC for model 11: 0.81898402098736
AUC for model 12: 0.8191990003459825
AUC for model 13: 0.7634236134671131
AUC for model 14: 0.5198234482017312
AUC for model 15: 0.7502208577004599
AUC for model 16: 0.7849736146427816
AUC for model 17: 0.6752434473283776
AUC for model 18: 0.7203101749058626
AUC for model 19: 0.7737678155745826
AUC for model 20: 0.8130250618905419
AUC for model 21: 0.8252217814398914
AUC for model 22: 0.8108954226191875


In [13]:
# 特徴量として使用する列名を作成
column_names = [f'pred_{i+1}' for i in range(len(pred_train_list))]

# 予測値を特徴量としてデータフレームを作成
train_x_2 = pd.DataFrame(
    {f'pred_{i+1}': pred_train_list[i] for i in range(len(pred_train_list))},
    columns=column_names
)

test_x_2 = pd.DataFrame(
    {f'pred_{i+1}': pred_test_list[i] for i in range(len(pred_test_list))},
    columns=column_names
)

In [14]:
# 2層目のモデル
# pred_train_2は、2層目のモデルの学習データのクロスバリデーションでの予測値
# pred_test_2は、2層目のモデルのテストデータの予測値
model_2 = Model2_Logistic()
pred_train_2, pred_test_2 = predict_cv(model_2, train_x_2, y, test_x_2)
print(f'AUC: {roc_auc_score(y, pred_train_2)}')

AUC: 0.7926020228214025


In [15]:
index = pd.read_csv('data/test.csv')['id'].values
df_submit = pd.DataFrame({
    "id": index,
    "prediction": pred_test_2
})

In [16]:
path = 'submission/submit_30_1.csv'

In [17]:
df_submit.to_csv(path, index=False, header=None)